## Imports

In [468]:
import pandas as pd
import numpy as np
import datetime, random

from tqdm import tqdm
from multiprocessing import Pool
#multiprocessing.cpu_count() --> 4
import time

## Reading in file; managing columns

In [491]:
%%time
df = pd.read_csv('~/Desktop/patr/StandardizingAKI/inpatient 2014-2018 creatinine.csv') #1441707, 4
df.pat_mrn_id = df.pat_mrn_id.str.strip('MR').astype('int')
df.time = pd.to_datetime(df.time)
print('size', df.shape)
print(df.dtypes)
df.columns = ['mrn',
              'enc',
              'time',
              'creat']
df.set_index(['mrn', 'enc'], inplace=True)

In [470]:
patient_dfs = df.groupby(['mrn'])
pat_df = patient_dfs.get_group(1000041)
backcalc_rows = np.array(pat_df.reset_index().drop_duplicates(['mrn', 'enc']).index)
times_to_consider = [pat_df.iloc[indx].time for indx in backcalc_rows]

new_rows = pat_df.iloc[backcalc_rows].copy()
for i in range(1,len(times_to_consider)):
    new_rows.iloc[i, new_rows.columns.get_loc('creat')] = pat_df.loc[np.logical_and(times_to_consider[i] - pat_df.time < datetime.timedelta(days=365),times_to_consider[i] - pat_df.time > datetime.timedelta(days=7)), 'creat'].mean()

mini_dfs = np.split(pat_df, backcalc_rows[1:])
mini_dfs = [pd.concat([new_rows.iloc[[indx]], dataframe]) for indx, dataframe in enumerate(mini_dfs)]
#mini_dfs[0]

## Creating $\Delta$creat, $\Delta$t, and first_enc (first encounter) variables

In [471]:
delta_df = df.groupby(['mrn', 'enc']).shift(-1) - df
df['delta_creat'] = delta_df['creat'].shift(1)
df['delta_time'] = delta_df['time'].shift(1)
#df[['delta_time, delta_creat']] = delta_df[['time', 'creatinine']]
firstencs = df.reset_index().drop_duplicates('mrn') #Similarly, df.groupby(['mrn']).head(1)
df['first_enc'] = [i in firstencs.index for i in range(df.shape[0])]
df.reset_index(inplace=True)
#df.head()

## Helper functions: add_rows(df), parallelize_analysis(df), ...

### add_rows()

    Input: Pandas data frame 

    Output: Pandas data frame (w/ extra dummy rows containing back-calculated values)

This is the function which adds dummy rows to the places where the delta creatinine/time values are not defined; in other words the location where the first encounter occurs. The dummy rows act as markers for the encounter and they also contain the back-calculated values for the patient. Generally, **no need to run this code directly**. Instead, use the parallelize_analysis function, which also takes in a data frame but will parallelize it to make it run faster. If the dataset is below $10^5$ rows, then *parallelize_analysis* will actually be slower... but it will run in a matter of seconds anyway.  

### parallelize_analysis()

This just returns the same as add_rows but parallelizes the code to make it faster. Modularity is our friend, this is why it is a separate function :)

### returnAKIpatients()

Finds the patients with AKI

### addDeltaCols()

In [479]:
def add_rows(df):
    '''
    Input: Pandas data frame
    Output: Pandas data frame
    
    Adds dummy rows to the places where the delta creatinine/time values are not defined; 
    in other words the location where the first encounter occurs. 
    The dummy rows act as markers for the encounter and they also contain the back-calculated values 
    for the patient. Generally, **no need to run this code directly**. 
    Instead, use the parallelize_analysis function, which also takes in a data frame 
    but will parallelize it to make it run faster. If the dataset is below $10^5$ rows, then 
    *parallelize_analysis* will actually be slower... but it will run in a matter of seconds anyway.  

    '''
    patient_dfs = df.groupby(['mrn'], sort=False) 
    patients = dict()
    
    for mrn, pat_df in patient_dfs:
        patients[mrn] = pat_df
        backcalc_rows = np.array(pat_df.reset_index().drop_duplicates(['mrn', 'enc']).index)
        times_to_consider = [pat_df.iloc[indx].time for indx in backcalc_rows]

        new_rows = pat_df.iloc[backcalc_rows].copy()
        for i in range(1,len(times_to_consider)):
            new_rows.iloc[i, new_rows.columns.get_loc('creat')] = pat_df.loc[np.logical_and(times_to_consider[i] - pat_df.time < datetime.timedelta(days=365),times_to_consider[i] - pat_df.time > datetime.timedelta(days=7)), 'creat'].mean()

        mini_dfs = np.split(pat_df, backcalc_rows[1:])
        mini_dfs = [pd.concat([new_rows.iloc[[indx]], dataframe]) for indx, dataframe in enumerate(mini_dfs)]
        pat_df = pd.concat(mini_dfs)
        patients[mrn] = pat_df
        
    return pd.concat(list(patients.values()))

def old_add_rows(df):
    '''
    Input: Pandas data frame
    Output: Pandas data frame
    
    Adds dummy rows to the places where the delta creatinine/time values are not defined; 
    in other words the location where the first encounter occurs. 
    The dummy rows act as markers for the encounter and they also contain the back-calculated values 
    for the patient. Generally, **no need to run this code directly**. 
    Instead, use the parallelize_analysis function, which also takes in a data frame 
    but will parallelize it to make it run faster. If the dataset is below $10^5$ rows, then 
    *parallelize_analysis* will actually be slower... but it will run in a matter of seconds anyway.  

    '''
    patient_dfs = df.groupby(['mrn'])
    patients = dict()
    for mrn, pat_df in patient_dfs:
        patients[mrn] = pat_df
        backcalc_rows = np.where(pat_df.delta_creat.isnull())[0]
        #backcalc_rows = np.array(pat_df.reset_index().drop_duplicates(['mrn', 'enc']).index)
        
        indx=None
        rows_to_add = list()
        for indx in backcalc_rows:
            lookback_indices = list()
            init_indx = indx

            if indx is not None:
                while (pat_df.iloc[indx].time - pat_df.iloc[indx-1].time) < datetime.timedelta(days=365) and pat_df.iloc[indx].mrn == pat_df.iloc[indx-1].mrn:
                    if pat_df.iloc[init_indx].time - pat_df.iloc[indx-1].time > datetime.timedelta(days=7):
                        lookback_indices.append(indx-1)
                    if indx == 0:
                        break
                    indx -= 1
            lookback_indices = np.sort(lookback_indices)
            new_row = pat_df.iloc[[init_indx]]
            new_row.loc[:, 'creat'] = pat_df.iloc[lookback_indices].creat.mean()
            rows_to_add.append(new_row)

        mini_dfs = np.split(pat_df, backcalc_rows)
        for indx, mini_df in enumerate(mini_dfs[1:]):
            mini_dfs[indx+1] = pd.concat([rows_to_add[indx], mini_df])
        pat_df = pd.concat(mini_dfs)
        patients[mrn] = pat_df
    return pd.concat(list(patients.values()))

def parallelize_analysis(df, func=add_rows, num_cores = 4):
    '''
    Input: dataframe, generic function, number of cpu processors to dedicate to parallelization
    Output: function applied to dataframe
    
    Generic parallelizing function, simple splits the dataframe, performs the operations on the split dataframes,
    
    '''
    split_dfs = np.array_split(df, num_cores)
    with Pool(num_cores) as p:
        result = p.map(func, split_dfs)
        df = pd.concat(result)
    return df

def returnAKIpatients(df, aki_calc_type = 'both'):
    #Redefine delta creat and delta time cols
    delta_df = d.groupby(['mrn', 'enc']).shift(-1) - df
    df['delta_creat'] = delta_df['creat'].shift(1)
    df['delta_time'] = delta_df['time'].shift(1)
    
    condition1 = np.logical_and(df.delta_creat > 0.3, df.delta_time < datetime.timedelta(hours=48))
    condition2 = np.logical_and(df.delta_creat > df.creat.shift(1)*0.5, df.delta_time < datetime.timedelta(days=7))    
    #Rolling Window conditions
    if aki_calc_type == 'both':
        df['aki'] = condition1 | condition2
    elif aki_calc_type == 'rolling_window':
        df['aki'] = (condition1 | condition2) & (df.delta_time != datetime.timedelta(0))
    elif aki_calc_type == 'back_calc':
        df['aki'] = condition2 & (df.delta_time == datetime.timedelta(0))
    return df
#Benchmark testing:
#For df of size 10000 add_rows(df) runs in 18.3 seconds, parallelize_analysis(df) runs in 11.5 s

### 2nd go w/ updated add_rows() code

Drops down to 52 minutes 24 seconds to run! Awesome!! :D - 52 minutes for 1441707 rows

In [433]:
%%time
d = add_rows(df)
d.head()
d.to_csv('modded_creat2ndgo.csv')

In [494]:
%%time
start = time.time()
split_dfs = np.array_split(df, 4)
with Pool(4) as p:
    result = p.map(add_rows, split_dfs)
    d4 = pd.concat(result)
d4.to_csv('modded_creat_parallel2.csv')
end = time.time()
#d3.to_csv('modded_creat2ndgo_parallel.csv')
#d3.head()

In [473]:
%%time
delta_df = d.groupby(['mrn', 'enc']).shift(-1) - d
d['delta_creat'] = delta_df['creat'].shift(1)
d['delta_time'] = delta_df['time'].shift(1)

firstencs = d.reset_index().drop_duplicates('mrn') #Similarly, df.groupby(['mrn']).head(1)
d['first_enc'] = [i in firstencs.index for i in range(d.shape[0])]
d.reset_index(inplace=True)
#d.head()

In [475]:
d2 = pd.read_csv('modded_creat.csv')
del d2['Unnamed: 0']
#d2.head()

In [455]:
df_aki = returnAKIpatients(d)

## Takes about 30 minutes to run on $25,000$ size dataset with 4 cores

In [5]:
dfs = [x for _, x in df.groupby('mrn')]
df_splits = list()
for i in range(0, len(dfs), int(len(dfs)/4)):
    df_splits.append((dfs[i:i+int(len(dfs)/4)]))

In [41]:
%%time
d_splits = list()
start = time.time()
for indx, dataframe in enumerate(dfs[:int(len(dfs)/4)]):
    loop_time = time.time()
    d_splits.append(add_rows(dataframe))
    print(indx, 'time per round:',time.time() - loop_time,'total time:', time.time()-start)

0 time per round: 0.019169092178344727 total time: 0.019516944885253906
1 time per round: 0.015413045883178711 total time: 0.03537797927856445
2 time per round: 0.02830219268798828 total time: 0.06418895721435547
3 time per round: 0.015829086303710938 total time: 0.08028388023376465
4 time per round: 0.07807302474975586 total time: 0.1587069034576416
5 time per round: 0.010429859161376953 total time: 0.1694028377532959
6 time per round: 0.011564016342163086 total time: 0.18135690689086914
7 time per round: 0.006329774856567383 total time: 0.18794989585876465
8 time per round: 0.00673675537109375 total time: 0.19494986534118652
9 time per round: 0.006356954574584961 total time: 0.20159173011779785
10 time per round: 0.0438690185546875 total time: 0.24574589729309082
11 time per round: 0.006635189056396484 total time: 0.2526218891143799
12 time per round: 0.031414031982421875 total time: 0.2843930721282959
13 time per round: 0.010061264038085938 total time: 0.2948319911956787
14 time per

119 time per round: 0.017604827880859375 total time: 6.661388874053955
120 time per round: 0.0076198577880859375 total time: 6.669142723083496
121 time per round: 0.007099151611328125 total time: 6.6763598918914795
122 time per round: 0.007928848266601562 total time: 6.684417724609375
123 time per round: 0.010615110397338867 total time: 6.6953349113464355
124 time per round: 0.07301807403564453 total time: 6.768581867218018
125 time per round: 0.00878000259399414 total time: 6.777829885482788
126 time per round: 0.019840002059936523 total time: 6.797976970672607
127 time per round: 0.009315967559814453 total time: 6.807500839233398
128 time per round: 0.008394956588745117 total time: 6.8162009716033936
129 time per round: 0.009808778762817383 total time: 6.826424837112427
130 time per round: 0.011348962783813477 total time: 6.838047742843628
131 time per round: 0.02093505859375 total time: 6.859280824661255
132 time per round: 0.008115768432617188 total time: 6.8677918910980225
133 tim

243 time per round: 0.009824991226196289 total time: 13.564401865005493
244 time per round: 0.013453006744384766 total time: 13.579099893569946
245 time per round: 0.009921789169311523 total time: 13.589240789413452
246 time per round: 0.01071619987487793 total time: 13.600146055221558
247 time per round: 0.009614229202270508 total time: 13.61081600189209
248 time per round: 0.03582286834716797 total time: 13.647278785705566
249 time per round: 0.010403156280517578 total time: 13.658143043518066
250 time per round: 0.01105189323425293 total time: 13.6698477268219
251 time per round: 0.011390924453735352 total time: 13.68203592300415
252 time per round: 0.00963592529296875 total time: 13.692012786865234
253 time per round: 0.012778043746948242 total time: 13.705162763595581
254 time per round: 0.13449406623840332 total time: 13.8402099609375
255 time per round: 0.007842063903808594 total time: 13.848643779754639
256 time per round: 0.009479999542236328 total time: 13.85870909690857
257 

361 time per round: 0.0074770450592041016 total time: 17.081759691238403
362 time per round: 0.009670734405517578 total time: 17.09196400642395
363 time per round: 0.012957096099853516 total time: 17.105069875717163
364 time per round: 0.007364749908447266 total time: 17.112900972366333
365 time per round: 0.00814509391784668 total time: 17.1213960647583
366 time per round: 0.018431901931762695 total time: 17.14023780822754
367 time per round: 0.03653311729431152 total time: 17.177150011062622
368 time per round: 0.008894920349121094 total time: 17.186462879180908
369 time per round: 0.009156227111816406 total time: 17.1960289478302
370 time per round: 0.00955510139465332 total time: 17.20594096183777
371 time per round: 0.00934600830078125 total time: 17.215758800506592
372 time per round: 0.013260841369628906 total time: 17.229480028152466
373 time per round: 0.01151895523071289 total time: 17.24124503135681
374 time per round: 0.008133888244628906 total time: 17.249711990356445
375 

483 time per round: 0.03649306297302246 total time: 20.18629002571106
484 time per round: 0.0106048583984375 total time: 20.197036743164062
485 time per round: 0.009669780731201172 total time: 20.206912755966187
486 time per round: 0.01163482666015625 total time: 20.219008684158325
487 time per round: 0.011832952499389648 total time: 20.23153066635132
488 time per round: 0.010565996170043945 total time: 20.24241805076599
489 time per round: 0.008774757385253906 total time: 20.251770973205566
490 time per round: 0.011141061782836914 total time: 20.26333498954773
491 time per round: 0.009562015533447266 total time: 20.27329182624817
492 time per round: 0.009124040603637695 total time: 20.28276801109314
493 time per round: 0.09427809715270996 total time: 20.377439737319946
494 time per round: 0.19957804679870605 total time: 20.577371835708618
495 time per round: 0.007110118865966797 total time: 20.584969997406006
496 time per round: 0.01707315444946289 total time: 20.602439880371094
497 t

...

25429 time per round: 0.02723407745361328 total time: 2017.52596783638
25430 time per round: 0.007623195648193359 total time: 2017.5339090824127
25431 time per round: 0.00934290885925293 total time: 2017.543450832367
25432 time per round: 0.024106979370117188 total time: 2017.5679488182068
25433 time per round: 0.008263111114501953 total time: 2017.5766298770905
25434 time per round: 0.008276939392089844 total time: 2017.585254907608
25435 time per round: 0.05587601661682129 total time: 2017.6413938999176
25436 time per round: 0.007773876190185547 total time: 2017.6495277881622
25437 time per round: 0.007568836212158203 total time: 2017.6572918891907
25438 time per round: 0.008066177368164062 total time: 2017.6656799316406
25439 time per round: 0.007658958435058594 total time: 2017.6736268997192
25440 time per round: 0.01416921615600586 total time: 2017.6882209777832
25441 time per round: 0.060148000717163086 total time: 2017.7486748695374
25442 time per round: 0.0072460174560546875 to

25556 time per round: 0.034258127212524414 total time: 2021.4515941143036
25557 time per round: 0.10752391815185547 total time: 2021.5594358444214
25558 time per round: 0.03586626052856445 total time: 2021.595633983612
25559 time per round: 0.007057905197143555 total time: 2021.6030097007751
25560 time per round: 0.006851911544799805 total time: 2021.6101887226105
25561 time per round: 0.007129192352294922 total time: 2021.617637872696
25562 time per round: 0.028183698654174805 total time: 2021.646069765091
25563 time per round: 0.007146120071411133 total time: 2021.653606891632
25564 time per round: 0.006928205490112305 total time: 2021.6608929634094
25565 time per round: 0.21770501136779785 total time: 2021.8789057731628
25566 time per round: 0.0070018768310546875 total time: 2021.8862218856812
25567 time per round: 0.007700204849243164 total time: 2021.8942308425903
25568 time per round: 0.007567882537841797 total time: 2021.9021668434143
25569 time per round: 0.020231962203979492 t

25671 time per round: 0.16739583015441895 total time: 2027.095797777176
25672 time per round: 0.007953882217407227 total time: 2027.1040477752686
25673 time per round: 0.022114038467407227 total time: 2027.126503944397
25674 time per round: 0.007426023483276367 total time: 2027.1342458724976
25675 time per round: 0.015094995498657227 total time: 2027.1496567726135
25676 time per round: 0.12603497505187988 total time: 2027.276027917862
25677 time per round: 0.007637739181518555 total time: 2027.284107685089
25678 time per round: 0.00722193717956543 total time: 2027.291664838791
25679 time per round: 0.007195949554443359 total time: 2027.2991588115692
25680 time per round: 0.021500110626220703 total time: 2027.3209178447723
25681 time per round: 0.00979304313659668 total time: 2027.3312058448792
25682 time per round: 0.010972976684570312 total time: 2027.3426859378815
25683 time per round: 0.008952856063842773 total time: 2027.3519277572632
25684 time per round: 0.007970809936523438 tota

25796 time per round: 0.16502594947814941 total time: 2030.805459022522
25797 time per round: 0.013059854507446289 total time: 2030.818925857544
25798 time per round: 0.007607936859130859 total time: 2030.8268728256226
25799 time per round: 0.011502742767333984 total time: 2030.8386678695679
25800 time per round: 0.11198091506958008 total time: 2030.9509069919586
25801 time per round: 0.007723093032836914 total time: 2030.9589657783508
25802 time per round: 0.008810997009277344 total time: 2030.9681558609009
25803 time per round: 0.017813920974731445 total time: 2030.9862637519836
25804 time per round: 0.024216175079345703 total time: 2031.010824918747
25805 time per round: 0.006906986236572266 total time: 2031.01806807518
25806 time per round: 0.006901979446411133 total time: 2031.0255298614502
25807 time per round: 0.007236003875732422 total time: 2031.0329859256744
25808 time per round: 0.010324954986572266 total time: 2031.0435600280762
25809 time per round: 0.00990915298461914 tot

25917 time per round: 0.006873130798339844 total time: 2035.2531509399414
25918 time per round: 0.0071659088134765625 total time: 2035.260931968689
25919 time per round: 0.0069391727447509766 total time: 2035.26802110672
25920 time per round: 0.009367942810058594 total time: 2035.2775008678436
25921 time per round: 0.01011037826538086 total time: 2035.2879140377045
25922 time per round: 0.016191959381103516 total time: 2035.3044278621674
25923 time per round: 0.008223295211791992 total time: 2035.3133656978607
25924 time per round: 0.007756948471069336 total time: 2035.3214507102966
25925 time per round: 0.00763392448425293 total time: 2035.3294019699097
25926 time per round: 0.009057998657226562 total time: 2035.338958978653
25927 time per round: 0.007665157318115234 total time: 2035.3470389842987
25928 time per round: 0.01856517791748047 total time: 2035.3659069538116
25929 time per round: 0.0286099910736084 total time: 2035.3949058055878
25930 time per round: 0.007723093032836914 to

In [ ]:
#df index 12708  took 153 seconds ... check that out 

In [42]:
%%time
d2_splits = list()
start = time.time()
for indx, dataframe in enumerate(dfs[int(len(dfs)/4):int(2*len(dfs)/4)]):
    loop_time = time.time()
    d2_splits.append(add_rows(dataframe))
    print(indx, 'time per round:',time.time() - loop_time,'total time:', time.time()-start)

0 time per round: 0.09045600891113281 total time: 0.09087014198303223
1 time per round: 0.01004481315612793 total time: 0.10125494003295898
2 time per round: 0.012927055358886719 total time: 0.1145620346069336
3 time per round: 0.04044914245605469 total time: 0.15528297424316406
4 time per round: 0.009689092636108398 total time: 0.16527009010314941
5 time per round: 0.018644094467163086 total time: 0.18426299095153809
6 time per round: 0.015630006790161133 total time: 0.20015811920166016
7 time per round: 0.014997005462646484 total time: 0.21539998054504395
8 time per round: 0.010094881057739258 total time: 0.2257990837097168
9 time per round: 0.0171358585357666 total time: 0.24324297904968262
10 time per round: 0.008905172348022461 total time: 0.2524418830871582
11 time per round: 0.09772300720214844 total time: 0.3505401611328125
12 time per round: 0.014525890350341797 total time: 0.3654789924621582
13 time per round: 0.013319015502929688 total time: 0.3793768882751465
14 time per ro

121 time per round: 0.7665200233459473 total time: 6.259822845458984
122 time per round: 0.015130758285522461 total time: 6.275184869766235
123 time per round: 0.008054018020629883 total time: 6.283612966537476
124 time per round: 0.007167816162109375 total time: 6.291075229644775
125 time per round: 0.5612027645111084 total time: 6.852550029754639
126 time per round: 0.24636125564575195 total time: 7.0991370677948
127 time per round: 0.011648893356323242 total time: 7.110953092575073
128 time per round: 0.06789183616638184 total time: 7.179141998291016
129 time per round: 0.006783962249755859 total time: 7.186194896697998
130 time per round: 0.006938934326171875 total time: 7.193389177322388
131 time per round: 0.00638127326965332 total time: 7.199968099594116
132 time per round: 0.010524988174438477 total time: 7.21073317527771
133 time per round: 0.014667034149169922 total time: 7.225622177124023
134 time per round: 0.0067348480224609375 total time: 7.232560873031616
135 time per ro

240 time per round: 0.03217005729675293 total time: 10.934741973876953
241 time per round: 0.00714111328125 total time: 10.942028045654297
242 time per round: 0.022361278533935547 total time: 10.964523077011108
243 time per round: 0.011719942092895508 total time: 10.976561069488525
244 time per round: 0.060771942138671875 total time: 11.037668943405151
245 time per round: 0.1195528507232666 total time: 11.157562971115112
246 time per round: 0.3422842025756836 total time: 11.50015902519226
247 time per round: 0.007955789566040039 total time: 11.50835108757019
248 time per round: 0.008263826370239258 total time: 11.517033100128174
249 time per round: 0.00976705551147461 total time: 11.527154922485352
250 time per round: 0.020308971405029297 total time: 11.547726154327393
251 time per round: 0.03026294708251953 total time: 11.578272104263306
252 time per round: 0.010344266891479492 total time: 11.589145183563232
253 time per round: 0.12494492530822754 total time: 11.71431303024292
254 tim

360 time per round: 0.019757986068725586 total time: 19.819683074951172
361 time per round: 0.006886720657348633 total time: 19.82677412033081
362 time per round: 0.006795167922973633 total time: 19.833739042282104
363 time per round: 0.04343080520629883 total time: 19.877302169799805
364 time per round: 0.00764012336730957 total time: 19.885271072387695
365 time per round: 0.010375022888183594 total time: 19.896056175231934
366 time per round: 0.016285181045532227 total time: 19.91255807876587
367 time per round: 0.12358307838439941 total time: 20.036520957946777
368 time per round: 0.009699106216430664 total time: 20.04652190208435
369 time per round: 0.006771087646484375 total time: 20.05365300178528
370 time per round: 0.02856922149658203 total time: 20.082529067993164
371 time per round: 0.01004171371459961 total time: 20.09271001815796
372 time per round: 0.00820302963256836 total time: 20.101518869400024
373 time per round: 0.007467031478881836 total time: 20.1094868183136
374 t

482 time per round: 0.0073091983795166016 total time: 23.831315994262695
483 time per round: 0.006825923919677734 total time: 23.838382244110107
484 time per round: 0.008504867553710938 total time: 23.847174882888794
485 time per round: 0.010289907455444336 total time: 23.85780096054077
486 time per round: 0.007761955261230469 total time: 23.86584997177124
487 time per round: 0.01992487907409668 total time: 23.886214017868042
488 time per round: 0.007199287414550781 total time: 23.89372181892395
489 time per round: 0.007812023162841797 total time: 23.901766061782837
490 time per round: 0.029047012329101562 total time: 23.931040048599243
491 time per round: 0.007355928421020508 total time: 23.938836097717285
492 time per round: 0.00718379020690918 total time: 23.946376085281372
493 time per round: 0.022322893142700195 total time: 23.96908402442932
494 time per round: 0.01318502426147461 total time: 23.98259401321411
495 time per round: 0.007428884506225586 total time: 23.990355968475342

...

25396 time per round: 0.07350802421569824 total time: 1592.0760431289673
25397 time per round: 0.007837772369384766 total time: 1592.0842740535736
25398 time per round: 0.0072901248931884766 total time: 1592.0918440818787
25399 time per round: 0.021117210388183594 total time: 1592.1133370399475
25400 time per round: 0.20445775985717773 total time: 1592.3184180259705
25401 time per round: 0.00788116455078125 total time: 1592.3267421722412
25402 time per round: 0.020041942596435547 total time: 1592.347608089447
25403 time per round: 0.050009965896606445 total time: 1592.39803814888
25404 time per round: 0.02163982391357422 total time: 1592.4200608730316
25405 time per round: 0.0071256160736083984 total time: 1592.4276640415192
25406 time per round: 0.008220195770263672 total time: 1592.4363760948181
25407 time per round: 0.0075168609619140625 total time: 1592.4443168640137
25408 time per round: 0.032099008560180664 total time: 1592.4768419265747
25409 time per round: 0.007932186126708984

25517 time per round: 0.049678802490234375 total time: 1596.5902879238129
25518 time per round: 0.02250504493713379 total time: 1596.6129899024963
25519 time per round: 0.0072100162506103516 total time: 1596.6203479766846
25520 time per round: 0.01289677619934082 total time: 1596.633381843567
25521 time per round: 0.0075762271881103516 total time: 1596.6414680480957
25522 time per round: 0.00785517692565918 total time: 1596.6498129367828
25523 time per round: 0.23759794235229492 total time: 1596.8876512050629
25524 time per round: 0.008164167404174805 total time: 1596.896269083023
25525 time per round: 0.21942400932312012 total time: 1597.1161410808563
25526 time per round: 0.034156084060668945 total time: 1597.1508071422577
25527 time per round: 0.016722917556762695 total time: 1597.167995929718
25528 time per round: 0.007748126983642578 total time: 1597.1761710643768
25529 time per round: 0.06546616554260254 total time: 1597.2420899868011
25530 time per round: 0.0073206424713134766 t

25633 time per round: 0.013828277587890625 total time: 1604.1013131141663
25634 time per round: 0.03995490074157715 total time: 1604.141704082489
25635 time per round: 0.009464025497436523 total time: 1604.1513850688934
25636 time per round: 0.008087158203125 total time: 1604.1596989631653
25637 time per round: 0.013688802719116211 total time: 1604.173595905304
25638 time per round: 0.015500068664550781 total time: 1604.1895968914032
25639 time per round: 0.1155397891998291 total time: 1604.3057570457458
25640 time per round: 0.008900165557861328 total time: 1604.3149881362915
25641 time per round: 0.050025224685668945 total time: 1604.3653910160065
25642 time per round: 0.009838104248046875 total time: 1604.3761510849
25643 time per round: 0.049935102462768555 total time: 1604.4263188838959
25644 time per round: 0.00980997085571289 total time: 1604.4365639686584
25645 time per round: 0.008530139923095703 total time: 1604.445688009262
25646 time per round: 0.02222895622253418 total tim

25751 time per round: 0.08854079246520996 total time: 1609.1291930675507
25752 time per round: 0.010390043258666992 total time: 1609.1400351524353
25753 time per round: 0.009979009628295898 total time: 1609.1504259109497
25754 time per round: 0.00923013687133789 total time: 1609.1600840091705
25755 time per round: 0.010525941848754883 total time: 1609.171028137207
25756 time per round: 0.010186910629272461 total time: 1609.1816101074219
25757 time per round: 0.010628938674926758 total time: 1609.1934459209442
25758 time per round: 0.17102694511413574 total time: 1609.364907026291
25759 time per round: 0.028981924057006836 total time: 1609.3940930366516
25760 time per round: 0.009869098663330078 total time: 1609.404247045517
25761 time per round: 0.16844487190246582 total time: 1609.5731961727142
25762 time per round: 0.9640979766845703 total time: 1610.5375349521637
25763 time per round: 0.010501861572265625 total time: 1610.5482409000397
25764 time per round: 0.013482093811035156 tota

25868 time per round: 0.04601097106933594 total time: 1615.9866330623627
25869 time per round: 0.023427963256835938 total time: 1616.010222196579
25870 time per round: 0.010827064514160156 total time: 1616.021539926529
25871 time per round: 0.13165879249572754 total time: 1616.1536359786987
25872 time per round: 0.03319907188415527 total time: 1616.1874780654907
25873 time per round: 0.009216070175170898 total time: 1616.1971609592438
25874 time per round: 0.009842872619628906 total time: 1616.2074508666992
25875 time per round: 0.009670019149780273 total time: 1616.217525959015
25876 time per round: 0.010023117065429688 total time: 1616.2281019687653
25877 time per round: 0.009197711944580078 total time: 1616.2374470233917
25878 time per round: 0.009867191314697266 total time: 1616.2474911212921
25879 time per round: 0.01075124740600586 total time: 1616.2588520050049
25880 time per round: 0.019695043563842773 total time: 1616.2789840698242
25881 time per round: 0.01172184944152832 tot

## RUN THIS OVERNIGHT - see whether it comes & how long it takes -- DIDN'T RUN 

In [191]:
%%time
def parallelize_analysis(list_of_dfs, func=add_rows, num_cores = 4):
    '''
    Input: dataframe, generic function, number of cpu processors to dedicate to parallelization
    Output: function applied to dataframe
    
    Generic parallelizing function, simple splits the dataframe, performs the operations on the split dataframes,
    
    '''
    with Pool(num_cores) as p:
        result = p.map(func, list_of_dfs)
        df = pd.concat(result)
    return df

#parallel_out = parallelize_analysis(dfs)
#parallel_out.to_csv('parallel_out.csv')

/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

  File "<frozen importlib._bootstrap>", line 1019, in _handle_fromlist
KeyboardInterrupt
  File "/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexes/base.py", line 567, in _shallow_copy_with_infer
    return Index(values, **attributes)
  File "/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexes/base.py", line 390, in __new__
    return Int64Index(data, copy=copy, dtype=dtype, name=name)
  File "/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexes/numeric.py", line 67, in __new__
    if issubclass(data.dtype.type, str):
KeyboardInterrupt


KeyboardInterrupt: 

In [173]:
%%time
d3_splits = list()
start = time.time()
loop_times = list()
#np.mean([loop_times[i] - loop_times[i-1] for i in range(1, len(loop_times))]) gives the avg time per 100 patients
for indx, dataframe in enumerate(dfs[int(2*len(dfs)/4):int(3*len(dfs)/4)]):
    d3_splits.append(add_rows(dataframe))
    if indx % 100 == 0:
        loop_times.append(time.time())
        print(indx, 'patients completed;','batch time:',time.time() - loop_times[int(indx/100)-1],'total time:', time.time()-start)

/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


In [157]:
%%time
d4_splits = list()
start = time.time()
loop_times4 = list()
#np.mean([loop_times[i] - loop_times[i-1] for i in range(1, len(loop_times))]) gives the avg time per 100 patients

for indx, dataframe in enumerate(dfs[int(3*len(dfs)/4):]):
    d4_splits.append(add_rows(dataframe))
    if indx % 100 == 0:
        loop_times4.append(time.time())
        print(indx, 'patients completed;','batch time:',time.time() - loop_times4[int(indx/100)-1],'total time:', time.time()-start)
        
#took 13 minutes! 
np.mean([loop_times4[i] - loop_times4[i-1] for i in range(1, len(loop_times4))])
#Takes 3 seconds / 100 patients on average (2.9931410610905944)

In [190]:
np.save('loop_times.npy', np.array(loop_times))

In [169]:
len(d_splits), len(d4_splits), len(d2_splits), len(d3_splits)

(25981, 25981, 25981, 1257)

In [476]:
out = pd.concat(d_splits + d2_splits + d3_splits + d4_splits)
print(out.shape)
#out.tail()

In [14]:
df_splits = np.array_split(df, 10)
d_splits = list()
df_splits[0].shape

(144171, 7)

In [13]:
%%time
d_splits.append(parallelize_analysis(df_splits[0])) #

/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:965: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

KeyboardInterrupt: 

In [15]:
%%time
d = parallelize_analysis(df)
d.to_csv('~/Desktop/patr/StandardizingAKI/modded_creat.csv')

/home/ishi/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/home/ishi/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/home/ishi/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead


CPU times: user 6.25 s, sys: 261 ms, total: 6.51 s
Wall time: 7min 47s


In [66]:
delta_d = d.groupby(['mrn', 'enc']).shift(-1) - d
d['delta_creat'] = delta_d['creat'].shift(1)
d['delta_time'] = delta_d['time'].shift(1)
#df[['delta_time, delta_creat']] = delta_df[['time', 'creatinine']]

#Rolling Window conditions
condition1 = np.logical_and(d.delta_creat > 0.3, d.delta_time < datetime.timedelta(hours=48))
condition2 = np.logical_and(d.delta_creat > d.creat.shift(1)*0.5, d.delta_time < datetime.timedelta(days=7))

## Two criterion for rolling-window definition of AKI:

#### *$creat \uparrow$ of 0.3 in < 48 hrs* OR *$creat \uparrow$ of 50% in < 7 days*

In [9]:
#Criterion 1
print(np.where(np.logical_and(df.delta_creat > 0.3, df.delta_time < datetime.timedelta(days=2))))

#Criterion 2
print(np.where(np.logical_and(df.delta_creat > df.creat.shift(1)*0.5, df.delta_time < datetime.timedelta(days=7))))

condition1 = np.logical_and(df.delta_creat > 0.3, df.delta_time < datetime.timedelta(hours=48))
condition2 = np.logical_and(df.delta_creat > df.creat.shift(1)*0.5, df.delta_time < datetime.timedelta(days=7))

(array([    95,    256,    282, ..., 372207, 372209, 372212]),)
(array([    95,    256,    354, ..., 371848, 371954, 371957]),)


In [5]:
#Quick question to ask: say a patient comes in on a separate encounter within 7 days
#and their creatinine has gone up by 50% since their previous encounter. Does that count as AKI?

#((df.groupby(['pat_mrn_id']).shift(-1) - df).time < datetime.timedelta(days=7)).sum()
#((df.groupby(['pat_mrn_id', 'pat_enc_csn_id']).shift(-1) - df).time < datetime.timedelta(days=7)).sum()

#df['AKI'] = np.logical_or(condition1, condition2)

#Question: Once you've got AKI you've got AKI for the rest of the encounter, right?
# df.loc['MR1000136']

#Condition 1 examples:
# MR1000136, MR1000468, MR1000507

#Condition 2 examples:
#MR1001546, MR1001806, 

#df[np.logical_xor(condition1, condition2)] gives unique examples of C1 or C2

In [11]:
#An idea of the numbers of those who have AKI according to the rolling window definition
print('creat > 0.3:', (df.delta_creat > 0.3).sum())
print('time < 48hrs:',(df.delta_time < datetime.timedelta(hours=48)).sum())
print('cond1:', np.logical_and(df.delta_creat > 0.3, df.delta_time < datetime.timedelta(hours=48)).sum())

print('creat_t > 1.5*creat_{t-1}:', (df.delta_creat > df.creat.shift(1)*0.5).sum())
print('time < 48hrs:',(df.delta_time < datetime.timedelta(days=7)).sum())
print('cond2:', np.logical_and(df.delta_creat > df.creat.shift(1)*0.5, df.delta_time < datetime.timedelta(days=7)).sum())

print('cond1 OR cond2:', np.logical_or(condition1, condition2).sum())

creat > 0.3: 18443
time < 48hrs: 305289
cond1: 17440
creat_t > 1.5*creat_{t-1}: 3289
time < 48hrs: 316436
cond2: 3265
cond1 OR cond2: 18057


%%time
df.reset_index(inplace=True)
patient_dfs = df.groupby(['mrn'])
patients = dict()
for mrn, pat_df in patient_dfs:
    patients[mrn] = pat_df
    backcalc_rows = np.where(pat_df.delta_creat.isnull())[0]

    indx=None
    rows_to_add = list()
    for indx in backcalc_rows:
        lookback_indices = list()
        init_indx = indx

        if indx is not None:
            while (pat_df.iloc[indx].time - pat_df.iloc[indx-1].time) < datetime.timedelta(days=365) and pat_df.iloc[indx].mrn == pat_df.iloc[indx-1].mrn:
                if pat_df.iloc[init_indx].time - pat_df.iloc[indx-1].time > datetime.timedelta(days=7):
                    lookback_indices.append(indx-1)
                if indx == 0:
                    break
                indx -= 1
        lookback_indices = np.sort(lookback_indices)
        new_row = pat_df.iloc[[init_indx]]
        new_row.loc[:, 'creat'] = pat_df.iloc[lookback_indices].creat.mean()
        rows_to_add.append(new_row)

    mini_dfs = np.split(pat_df, backcalc_rows)
    for indx, mini_df in enumerate(mini_dfs[1:]):
        mini_dfs[indx+1] = pd.concat([rows_to_add[indx], mini_df])
    pat_df = pd.concat(mini_dfs)
    patients[mrn] = pat_df
pd.concat(list(patients.values()))

In [10]:
def eGFR(creat, age, black, female):
    '''
    Calculates the estimated glomerular filtration rate based on the serum creatinine levels, age, sex, and race (black or not black);
    Based on the formula in the paper A New Equation to Estimate Glomerular Filtration Rate (Levey et. Al, 2009) linked below
    
    https://pubmed.ncbi.nlm.nih.gov/19414839/
    
    '''
    #Term 2 - np.clip(creat/(0.9-0.2*female, a_min=1, a_max=None) is the same as taking min(1, creat/k)
    #Term 3 - np.clip(creat/(0.9-0.2*female, a_min=None, a_max=None) is the same as taking max(1, creat/k)
    #where k is the data-derived constant given in the paper: 0.7 for females and 0.9 for males
    
    return 141*(np.clip(creat/(0.9-0.2*female), a_min=1, a_max=None)**(-0.411+0.082*female))*(np.clip(creat/(0.9-0.2*female), a_min=None, a_max=1)**-1.209)*(0.993**age)*(1+female*0.018)*(1+black*0.159)

#Sample test data
creat = np.random.normal(loc=1, scale=0.2, size=10)
age = np.random.normal(loc=55, scale=10, size=10)
black = np.random.rand(10) > 0.5
female = np.random.rand(10) > 0.5

eGFR(creat, age, black, female) 
#values seem pretty reasonable (80-120)

array([113.89903888, 100.8786952 ,  87.46893682,  97.14803991,
        91.94999961, 112.69153215,  96.81254917, 129.33209018,
       126.9104726 ,  93.73315848])

In [477]:
df['age'] = None
df['sex'] = None
mrn_gb = df.groupby(['mrn'])
tmp = mrn_gb.head(1)
tmp['sex'] = np.random.rand(tmp.shape[0]) > 0.5
tmp['age'] = np.random.normal(loc=50, scale=10, size=tmp.shape[0])
df['age'] = tmp['age'] #So this works! I can match by index the ages & sex
df['sex'] = tmp['sex'] #even though df and tmp are different shapes... awesome! 
df['age'] = mrn_gb['age'].transform(lambda x: x.ffill())
df['sex'] = mrn_gb['sex'].transform(lambda x: x.ffill())
#df.head()

/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
/Users/saranmedical-smile/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


#For pat mrn 212
##0 --> 0
#11 --> 0.29818181818181827
#18 --> 0.31500000000000006
#26 --> 0.33666666666666667

pat_df = patient_dfs.get_group(212)
#backcalc_rows = np.where(np.logical_and(pat_df.delta_creat.isnull(), ~pat_df.first_enc))[0]
backcalc_rows = np.where(pat_df.delta_creat.isnull())[0]
print(backcalc_rows)

indx=None
rows_to_add = list()
for indx in backcalc_rows:
    lookback_indices = list()
    init_indx = indx
    
    if indx is not None:
        while (pat_df.iloc[indx].time - pat_df.iloc[indx-1].time) < datetime.timedelta(days=365) and pat_df.iloc[indx].mrn == pat_df.iloc[indx-1].mrn:
            if pat_df.iloc[init_indx].time - pat_df.iloc[indx-1].time > datetime.timedelta(days=7):
                lookback_indices.append(indx-1)
            if indx == 0:
                break
            indx -= 1
    lookback_indices = np.sort(lookback_indices)
    new_row = pat_df.iloc[[init_indx]]
    new_row.loc[:, 'creat'] = pat_df.iloc[lookback_indices].creat.mean()
    rows_to_add.append(new_row)
    
mini_dfs = np.split(pat_df, backcalc_rows)

for indx, mini_df in enumerate(mini_dfs[1:]):
    mini_dfs[indx+1] = pd.concat([rows_to_add[indx], mini_df])
pat_df = pd.concat(mini_dfs)